<center><h1> LAB 3 - OBJECTS TRACKING </h></center>
<center>Fromsa T. Negasa, Nadeer Hassan</center>
<center>Photonics for Security, Reliability, and Safety (PSRS)</center>
<center>Medical Biometrics</center>
<center>Yasmina CHENOUNE, Instructor</center>
<center>28<sup>th</sup> October 2024</center>

### Objective
This lab aims to implement video handling, image extraction, object tracking, and synthetic video generation using Python.

In [1]:
import cv2
import os

import numpy as np
import matplotlib.pyplot as plt

from matplotlib import animation
from IPython.display import HTML

from skimage import exposure, morphology
from skimage.segmentation import clear_border
from scipy.ndimage import binary_fill_holes

### 1 Video Sequences Reading and Playing
Load a video sequence (fly.avi or STGEORGES.avi), read it and play it from Matlab or Python.

In [2]:
# Load video
video_path = 'fly.avi' 
cap = cv2.VideoCapture(video_path)

# Collect frames from the video
frames = []
while True:
    ret, frame = cap.read()
    if not ret:
        break
    frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)  # Convert to RGB for display
    frames.append(frame_rgb)

cap.release()

# Define the figure and animation function
fig, ax = plt.subplots()
ax.axis('off')
im = ax.imshow(frames[0])

def animate(i):
    im.set_array(frames[i])
    return [im]

# Create the animation (from matplotlib import animation)
ani = animation.FuncAnimation(fig, animate, frames=len(frames), interval=50, blit=True)
plt.close()  # Prevent duplicate output

# Display the animation in the notebook (from IPython.display import HTML)
HTML(ani.to_jshtml())

### 2 Extract Images from Video or Create a Video Sequence
- Extract all the images from a video sequence and store them into 2D grayscale images 
- Create two (.avi) video files from the given images (TAXI or PIETON) 
- Play the obtained videos 
- Try to play the videos using a modified frame rate (/2 or /3)

In [3]:
def load_frames(folder_path, prefix='PIETON', extension='bmp'):
    frames = []
 
    # Custom sort function to sort based on the numerical part of the filename
    def sort_key(filename):
        # Ensure the filename matches the specified prefix and extension
        if filename.startswith(prefix) and filename.endswith(extension):
            # Extract the number from the filename
            number_part = filename[len(prefix):-len(extension)-1]  # Adjust for prefix and extension length
            return int(number_part)
        return float('inf')  # Assign a large value to any non-matching files

    # Get a list of files matching the prefix and extension
    file_list = [f for f in os.listdir(folder_path) if f.startswith(prefix) and f.endswith(extension)]
    
    # Sort files using the custom sort key
    for filename in sorted(file_list, key=sort_key):
        img_path = os.path.join(folder_path, filename)
        gray_frame = cv2.imread(img_path, cv2.IMREAD_GRAYSCALE)
        frames.append(gray_frame)
    
    return frames

In [10]:
# Function to display a sequence of frames as a video animation
def display_animation(frames, interval=100, export_path=None, fps=10):
    fig, ax = plt.subplots()
    ax.axis('off')
    im = ax.imshow(frames[0], cmap='gray')
    
    def animate(i):
        im.set_array(frames[i])
        return [im]

    ani = animation.FuncAnimation(fig, animate, frames=len(frames), interval=interval, blit=False)
    plt.close()  # Prevent duplicate output
    
    # Export to video if export_path is specified
    height, width = frames[0].shape[:2]
    
    if export_path is not None:
        fourcc = cv2.VideoWriter_fourcc(*'XVID')
        out = cv2.VideoWriter(export_path, fourcc, fps, (width, height), isColor=True) # isColor=True for RGB
        for frame in frames:
            # Ensure the frame is in the right format for VideoWriter
            out.write(frame)
        out.release()
        print(f"Video saved as {export_path}")
    
    return HTML(ani.to_jshtml())

In [5]:
# Paths to folders containing frames
taxi_folder = 'TAXI'; pieton_folder = 'PIETON'  

# Load frames from each folder
taxi_frames=  load_frames(taxi_folder, prefix="TAXI_", extension="BMP")
pieton_frames = load_frames(pieton_folder, prefix="PIETON", extension="bmp")

# Display the animations for TAXI and PIETON frames
print("Displaying video:")
display_animation(taxi_frames, interval=100, export_path="taxi_video.avi", fps=10) # export_path='pieton_video.avi' is optional

Displaying video:
Video saved as taxi_video.avi


### 3 Objects Tracking on PIETON Video Sequence
Objective: Automatically segment and track two persons in the video, displaying their trajectories.

- Pre-process: Apply filters or transformations as needed.
- Segmentation and Tracking: Track and display trajectories.
- Visualize Trajectories: Show the trajectory of each person overlaid on the final frame.
- Bounding Box Visualization: Draw a bounding box around the tracked objects in each frame and save as a new video.

#### Pre-Processing

In [6]:
def preprocess_image(image):
    # Adjust contrast similar (from skimage import exposure)
    image_adjusted = exposure.rescale_intensity(image, in_range='image', out_range=(0, 255)).astype(np.uint8)
    
    # Thresholding
    _, bw = cv2.threshold(image_adjusted, 90, 255, cv2.THRESH_BINARY)
    
    # Invert the mask
    bw = cv2.bitwise_not(bw)
    
    # Fill holes (from scipy.ndimage import binary_fill_holes)
    bw_filled = binary_fill_holes(bw).astype(np.uint8) * 255
    
    # Clear borders (from skimage.segmentation import clear_border)
    bw_no_border = clear_border(bw_filled).astype(np.uint8) * 255

    # Erode with line structuring element
    se_erode = cv2.getStructuringElement(cv2.MORPH_RECT, (1, 10))
    bw_eroded = cv2.erode(bw_no_border, se_erode)

    # Open mask with line structuring element
    se_open = cv2.getStructuringElement(cv2.MORPH_RECT, (1, 15))
    bw_opened = cv2.morphologyEx(bw_eroded, cv2.MORPH_OPEN, se_open)
    
    # Remove small objects (from skimage import morphology)
    bw_final = morphology.remove_small_objects(bw_opened > 0, min_size=150, connectivity=8)
    bw_final = (bw_final * 255).astype(np.uint8)
    
    # Create masked image
    masked_image = image.copy()
    masked_image[bw_final == 0] = 0
    
    return bw_final, masked_image

#### Tracking

In [7]:
def track_objects_with_smooth_trajectory(frames):
    trajectories = [[], []]  # Tracking for two persons
    tracked_frames = []

    for frame in frames:
        # Apply preprocessing
        bw, preprocessed_frame = preprocess_image(frame)
        
        # Find contours on the preprocessed binary image
        contours, _ = cv2.findContours(bw, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
        
        # Filter contours for the two largest (assumed to be persons)
        contours = sorted(contours, key=cv2.contourArea, reverse=True)[:2]
        
        # Draw bounding boxes and track trajectories
        output_frame = cv2.cvtColor(frame, cv2.COLOR_GRAY2BGR)  # Convert to BGR for drawing
        for i, cnt in enumerate(contours):
            x, y, w, h = cv2.boundingRect(cnt)
            cv2.rectangle(output_frame, (x, y), (x + w, y + h), (0, 255, 0), 2)
            
            # Track the center of each bounding box
            center = (x + w // 2, y + h // 2)
            trajectories[i].append(center)
            
            # Draw a line to show the trajectory
            if len(trajectories[i]) > 1:
                for j in range(1, len(trajectories[i])):
                    cv2.line(output_frame, trajectories[i][j - 1], trajectories[i][j], (255, 0, 0), 2)

        tracked_frames.append(output_frame)
   
    return tracked_frames

#### Displaying the result

In [11]:
# Apply tracking on PIETON frames
tracked_pieton_frames = track_objects_with_smooth_trajectory(pieton_frames)

# Display tracking animation 
display_animation(tracked_pieton_frames, interval=100, export_path="tracking_video.avi", fps=10)

Video saved as tracking_video.avi


### 4 Create Synthetic Images with Moving Objects
- Generate Synthetic Sequence: Create an n x m x nb array representing frames with moving objects.
- Apply Transformations: Move the object across frames to simulate motion.
- Save and Play: Save the synthetic sequence as a video and play it.

In [9]:
# Parameters for synthetic image sequence
n, m = 100, 100             # Dimensions of each frame
nb_frames = 50              # Number of frames
object_size = 10            # Size of the object (radius for circle)
translation_step = 2        # Pixels to move per frame
rotation_angle_step = 5     # Degrees to rotate per frame

# Generate frames with a moving and rotating object
frames = []
for i in range(nb_frames):
    frame = np.zeros((n, m), dtype=np.uint8)  # Create a black frame
    center_x = (i * translation_step) % n  # Move object horizontally
    center_y = (i * translation_step) % m  # Move object vertically
    angle = i * rotation_angle_step  # Rotation angle for current frame

    # Create a moving and rotating square
    object_frame = np.zeros((n, m), dtype=np.uint8)
    cv2.rectangle(object_frame, (center_x - object_size, center_y - object_size),
                  (center_x + object_size, center_y + object_size), 255, -1)
    rotation_matrix = cv2.getRotationMatrix2D((center_x, center_y), angle, 1)
    rotated_frame = cv2.warpAffine(object_frame, rotation_matrix, (m, n))

    # Add the rotated object to the main frame
    frames.append(rotated_frame)

# Display the synthetic animation using your display_animation function
display_animation(frames, interval=100, export_path='synthetic_movement.avi', fps=10) # export_path='synthetic_movement.avi'

Video saved as synthetic_movement.avi
